In [131]:
from pyspark.sql import SparkSession
from pyspark.sql.functions import *
from pyspark.sql.types import *
import pandas as pd
import numpy as np

spark = SparkSession.\
        builder.\
        appName("subbreddit_count").\
        master("spark://spark-master:7077").\
        getOrCreate()

In [145]:
all_subbreddits = []
datedict = {}

In [177]:
PATH = 'hdfs://192.168.2.237:9000/reddit/rc-2015*.csv.bz2'


In [178]:
#Load the CSV file from HDFS

schema = StructType([\
    StructField("date", StringType(), True),\
    StructField("subbreddit", StringType(), True)])

df = spark.read\
    .option("header", "false")\
    .schema(schema)\
    .csv(PATH)\
    .withColumn('date', substring('date', 1, 7))\
    .cache()
#df.take(5)

In [179]:
# create a list of all the months

datelist = pd.date_range(start="2015-01",end="2015-12")

months = []
for i in range(1,len(datelist)):
    month = str(datelist[i])[0:7]
    if month not in months:
        months.append(month)
months

['2015-01',
 '2015-02',
 '2015-03',
 '2015-04',
 '2015-05',
 '2015-06',
 '2015-07',
 '2015-08',
 '2015-09',
 '2015-10',
 '2015-11',
 '2015-12']

In [180]:


for month in months:
    print(month)
    toplist= df.where(col("date") == month)\
            .groupBy('subbreddit')\
            .count()\
            .orderBy('count', ascending=False)\
            .limit(10)\
            .collect()

    subdict = {}
    for i in range(10):
        subdict[toplist[i][0]] = toplist[i][1]
        datedict[month] = subdict
    for subbreddit in subdict.keys():
        if subbreddit not in all_subbreddits:
            all_subbreddits.append(subbreddit)
print("all: ", all_subbreddits)

2015-01


Py4JJavaError: An error occurred while calling o2952.collectToPython.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 202.0 failed 4 times, most recent failure: Lost task 0.6 in stage 202.0 (TID 20274) (192.168.2.237 executor 14672): java.io.IOException: No space left on device
	at sun.nio.ch.FileDispatcherImpl.write0(Native Method)
	at sun.nio.ch.FileDispatcherImpl.write(FileDispatcherImpl.java:60)
	at sun.nio.ch.IOUtil.writeFromNativeBuffer(IOUtil.java:93)
	at sun.nio.ch.IOUtil.write(IOUtil.java:65)
	at sun.nio.ch.FileChannelImpl.write(FileChannelImpl.java:211)
	at org.apache.spark.storage.CountingWritableChannel.write(DiskStore.scala:339)
	at java.nio.channels.Channels.writeFullyImpl(Channels.java:78)
	at java.nio.channels.Channels.writeFully(Channels.java:101)
	at java.nio.channels.Channels.access$000(Channels.java:61)
	at java.nio.channels.Channels$1.write(Channels.java:174)
	at java.io.BufferedOutputStream.write(BufferedOutputStream.java:122)


In [ ]:
# We need to get all the subbreddits that has ever been in the top 10
# for each month:


In [181]:
# make the dict to a panda dataframe for animation plot
panda_data = pd.DataFrame.from_dict(datedict).T.fillna(0)
panda_data
#panda_data.to_csv(r'reddit_data.csv', index = False)

reddit.com   programming   science   features     ja   freeculture  \
2007-01      70939.0        7650.0    2018.0      156.0  138.0         101.0   
2007-02      81879.0       10146.0    2605.0      169.0   85.0         141.0   
2007-03      95443.0       11715.0    3946.0      337.0  216.0         175.0   
2007-04     109743.0       12272.0    3588.0      206.0  178.0         119.0   
2007-05     149922.0       14209.0    4817.0      238.0  161.0         181.0   
...              ...           ...       ...        ...    ...           ...   
2014-08          0.0           0.0       0.0        0.0    0.0           0.0   
2014-09          0.0           0.0       0.0        0.0    0.0           0.0   
2014-10          0.0           0.0       0.0        0.0    0.0           0.0   
2014-11          0.0           0.0       0.0        0.0    0.0           0.0   
2014-12          0.0           0.0       0.0        0.0    0.0           0.0   

          lipstick.com   joel   request    de  ...   friendsafari   dogecoin  \
2007-01           98.0   54.0      36.0  34.0  ...            0.0        0.0   
2007-02          247.0   76.0       0.0   0.0  ...            0.0        0.0   
2007-03          262.0   74.0      52.0   0.0  ...            0.0        0.0   
2007-04          154.0   70.0       0.0   0.0  ...            0.0        0.0   
2007-05            0.0   54.0       0.0   0.0  ...            0.0        0.0   
...                ...    ...       ...   ...  ...            ...        ...   
2014-08            0.0    0.0       0.0   0.0  ...            0.0        0.0   
2014-09            0.0    0.0       0.0   0.0  ...            0.0        0.0   
2014-10            0.0    0.0       0.0   0.0  ...            0.0        0.0   
2014-11            0.0    0.0       0.0   0.0  ...            0.0        0.0   
2014-12            0.0    0.0       0.0   0.0  ...            0.0        0.0   

              nba   hockey   soccer   DotA2   fantasyfootball  \
2007-01       0.0      0.0      0.0     0.0               0.0   
2007-02       0.0      0.0      0.0     0.0               0.0   
2007-03       0.0      0.0      0.0     0.0               0.0   
2007-04       0.0      0.0      0.0     0.0               0.0   
2007-05       0.0      0.0      0.0     0.0               0.0   
...           ...      ...      ...     ...               ...   
2014-08       0.0      0.0      0.0     0.0               0.0   
2014-09       0.0      0.0      0.0     0.0          639533.0   
2014-10       0.0      0.0      0.0     0.0          590381.0   
2014-11  448653.0      0.0      0.0     0.0               0.0   
2014-12       0.0      0.0      0.0     0.0               0.0   

          DestinyTheGame       CFB      news  
2007-01              0.0       0.0       0.0  
2007-02              0.0       0.0       0.0  
2007-03              0.0       0.0       0.0  
2007-04              0.0       0.0       0.0  
2007-05              0.0       0.0       0.0  
...                  ...       ...       ...  
2014-08              0.0       0.0       0.0  
2014-09         475409.0       0.0       0.0  
2014-10         599409.0       0.0       0.0  
2014-11              0.0  564319.0       0.0  
2014-12         600385.0       0.0  491026.0  

[96 rows x 50 columns]

In [182]:
import bar_chart_race as bcr
df = panda_data
bcr.bar_chart_race(df=df, title='posts per day', n_bars=10,filename=None)

/home/ubuntu/.local/lib/python3.8/site-packages/bar_chart_race/_make_chart.py:286: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_yticklabels(self.df_values.columns)
/home/ubuntu/.local/lib/python3.8/site-packages/bar_chart_race/_make_chart.py:287: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_xticklabels([max_val] * len(ax.get_xticks()))


In [ ]:
import bar_chart_race as bcr
df = panda_data
bcr.bar_chart_race(df=df, title='posts per day', n_bars=10,filename='reddit_all.mp4')

In [7]:
#print(datedict['2013-12-01'][" AskReddit"])

In [4]:
import bar_chart_race as bcr
df = bcr.load_dataset('covid19_tutorial')
bcr.bar_chart_race(df=df, filename=None)

In [3]:
import bar_chart_race as bcr
df = bcr.load_dataset('covid19_tutorial')
bcr.bar_chart_race(
    df=df,
    filename='covid19_horiz.mp4',
    orientation='h',
    sort='desc',
    n_bars=6,
    fixed_order=False,
    fixed_max=True,
    steps_per_period=10,
    interpolate_period=False,
    label_bars=True,
    bar_size=.95,
    period_label={'x': .99, 'y': .25, 'ha': 'right', 'va': 'center'},
    period_fmt='%B %d, %Y',
    period_summary_func=lambda v, r: {'x': .99, 'y': .18,
                                      's': f'Total deaths: {v.nlargest(6).sum():,.0f}',
                                      'ha': 'right', 'size': 8, 'family': 'Courier New'},
    perpendicular_bar_func='median',
    period_length=500,
    figsize=(5, 3),
    dpi=144,
    cmap='dark12',
    title='COVID-19 Deaths by Country',
    title_size='',
    bar_label_size=7,
    tick_label_size=7,
    shared_fontdict={'family' : 'Helvetica', 'color' : '.1'},
    scale='linear',
    writer=None,
    fig=None,
    bar_kwargs={'alpha': .7},
    filter_column_colors=False)

/home/ubuntu/.local/lib/python3.8/site-packages/bar_chart_race/_make_chart.py:286: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_yticklabels(self.df_values.columns)
/home/ubuntu/.local/lib/python3.8/site-packages/bar_chart_race/_make_chart.py:287: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_xticklabels([max_val] * len(ax.get_xticks()))
findfont: Font family ['Courier New'] not found. Falling back to DejaVu Sans.


In [ ]:
df.groupBy('subbreddit').count().orderBy('count', ascending=False).show()

In [130]:
# release the cores for another application!
spark.stop()